This file can be used to reproduce figures 5-6 from the paper (and equivalent figures). For details on the data used, please see the main reproducibility document. 

In [ ]:
import numpy as np
import pickle
import pandas as pd
from functools import partial
import glob
import seaborn as sbs
import matplotlib.pyplot as plt

from scipy.stats import kendalltau, rankdata

font = {'size'   : 24}

plt.rc('font', **font)

#Font-requirement for GECCO
import matplotlib
matplotlib.rcParams['pdf.fonttype'] = 42
matplotlib.rcParams['ps.fonttype'] = 42

In [ ]:
algorithms = ['DifferentialEvolution', 'ConfiguredPSO', 'modcma']

In [ ]:
type_ = 'long'

In [ ]:
dt = pd.DataFrame()
for fid in range(1,25):
    dt = dt.append(pd.read_csv(f"RF_Results_norm/{type_}/Real/F{fid}_{a1}_{a2}.csv", index_col=0))

In [ ]:
dt_mean = dt[['Real', 'Predicted', 'sp', 'fid']].groupby(['sp', 'fid']).agg(np.mean)

In [ ]:
dt_mean = dt_mean.reset_index()

In [ ]:
splitpoints = np.unique(dt_mean['sp'])

In [ ]:
rel_benefit = np.zeros(shape=(24,len(splitpoints)))* np.nan

In [ ]:
for fid in range(1,25):
    vals = dt_mean[dt_mean['fid'] == fid]['Real']
    rel_benefit[fid-1,:] = np.pad(vals, constant_values = np.nan, pad_width = [(0,len(splitpoints) - len(vals))])

In [ ]:
plt.figure(figsize=(16,9))
sbs.heatmap(rel_benefit, center=0, linewidths=0.0, rasterized=True)
plt.xticks(range(0,187, 20), [int(splitpoints[i]) for i in range(0,187, 20)] )
plt.yticks(np.arange(0.5,24.5,1), range(1,25) , rotation=0)
plt.xlabel("Switch point")
plt.ylabel("Function ID")
plt.tight_layout()
plt.savefig(f"Paper_Figures/Heatmap_{a1}_{a2}_overall_benefit.pdf")

In [ ]:
def create_heatmap(a1,a2, use_predicted = False):
    dt = pd.DataFrame()
    for fid in range(1,25):
        try:
            dt = dt.append(pd.read_csv(f"RF_Results_norm/{type_}/Real/F{fid}_{a1}_{a2}.csv", index_col=0))
        except:
            print(fid)
    dt_mean = dt[['Real', 'Predicted', 'sp', 'fid']].groupby(['sp', 'fid']).agg(np.mean)
    dt_mean = dt_mean.reset_index()
    
    rel_benefit = np.zeros(shape=(24,len(splitpoints)))* np.nan
    for fid in range(1,25):
        if use_predicted:
            vals = dt_mean[dt_mean['fid'] == fid]['Predicted']
        else:
            vals = dt_mean[dt_mean['fid'] == fid]['Real']
        rel_benefit[fid-1,:] = np.pad(vals, constant_values = np.nan, pad_width = [(0,len(splitpoints) - len(vals))])
        
    plt.figure(figsize=(16,9))
    sbs.heatmap(rel_benefit, center=0, linewidths=0.0, rasterized=True)
    plt.xticks(range(0,187, 20), [int(splitpoints[i]) for i in range(0,187, 20)] )
    plt.yticks(np.arange(0.5,24.5,1), range(1,25) , rotation=0)
    plt.xlabel("Switch point")
    plt.ylabel("Function ID")
    plt.tight_layout()
    if use_predicted:
        plt.savefig(f"Paper_Figures/Heatmap_{a1}_{a2}_predicted_benefit.pdf")
    else:
        plt.savefig(f"Paper_Figures/Heatmap_{a1}_{a2}_overall_benefit.pdf")


In [ ]:
for a1 in algorithms:
    for a2 in algorithms:
        create_heatmap(a1, a2)

In [ ]:
for a1 in algorithms:
    for a2 in algorithms:
        create_heatmap(a1, a2, True)

In [ ]:
matrix_rel = np.zeros((3,3))
use_predicted = False

for i, a1 in enumerate(algorithms):
    for j, a2 in enumerate(algorithms):
        dt = pd.DataFrame()
        for fid in range(1,25):
            try:
                dt = dt.append(pd.read_csv(f"RF_Results_norm/{type_}/Real/F{fid}_{a1}_{a2}.csv", index_col=0))
            except:
                print(fid)
        dt_mean = dt[['Real', 'Predicted', 'sp', 'fid']].groupby(['sp', 'fid']).agg(np.mean)
        dt_mean = dt_mean.reset_index()

        rel_benefit = np.zeros(shape=(24,len(splitpoints)))* np.nan
        for fid in range(1,25):
            if use_predicted:
                vals = dt_mean[dt_mean['fid'] == fid]['Predicted']
            else:
                vals = dt_mean[dt_mean['fid'] == fid]['Real']
            rel_benefit[fid-1,:] = np.pad(vals, constant_values = np.nan, pad_width = [(0,len(splitpoints) - len(vals))])
        val1 = np.sum(rel_benefit > 0)
        val2 = np.sum(rel_benefit <= 0)
        
        matrix_rel[i,j] = val1 / (val1 + val2)

In [ ]:
matrix_rel

In [ ]:
matrix_rel

Set use_predicted to true or false to get either of the next two plots

In [ ]:
plt.figure(figsize=(16,10))
plt.imshow(matrix_rel, vmin=0, vmax=1)
plt.xticks([0,1,2], algorithms, rotation=-10)
plt.yticks([0,1,2], algorithms)
plt.colorbar()
plt.xlabel("Algorithm 2")
plt.ylabel("Algorithm 1")
plt.savefig("Paper_Figures/Matrix_Fraction_Benefits_predicted.pdf")

In [ ]:
plt.figure(figsize=(16,5))
sbs.heatmap(matrix_rel, vmin=0, vmax=1, cmap='viridis')
plt.xticks([0.5,1.5,2.5], algorithms, rotation=0)
plt.yticks([0.5,1.5,2.5], algorithms, rotation=0)
# sbs.colorbar()
plt.xlabel("Algorithm 2")
plt.ylabel("Algorithm 1")
plt.tight_layout()
plt.savefig("Paper_Figures/Matrix_Fraction_Benefits.pdf")